In [1]:
import pandas as pd
import numpy as np
import states_abbrevs
from states_abbrevs import dict2
import glob

In [73]:
path = r"C:\Users\Steven Lantigua\Desktop\7ParkCP\incomedata" 
files = glob.glob(path + "/*.csv")
years = ['2013','2014','2015','2016','2017','2018','2019']
li=[]

for (f,y) in zip(files,years):
    df = pd.read_csv(f, index_col=None, header=0)
    df = df.loc[1:] #removes unnecessary column description
    df['Year'] = y
    li.append(df)

frame = pd.concat(li, axis=0, ignore_index=True)
framec = frame.copy()

In [74]:
income = framec.loc[:,['Year','NAME','DP03_0051E','DP03_0062E']]
income.rename(columns={ 'NAME':'County','DP03_0051E':'Total_Households', 'DP03_0062E':'Med_income'},inplace=True)

### fixing 'Location' format

In [75]:
income['county']=income['County'].str.split(',',1,expand=True)[0]
income['state'] = income['County'].str.split(',',1,expand=True)[1]
income['state'] = income['state'].apply(lambda x: x.strip())
income['state'] = income['state'].map(dict2)
income['County'] = income['county'] + ',' + income['state']
income.drop('county',axis=1,inplace=True)


 ### changing 'income' and 'total households' to integers

In [76]:
income['Med_income']=income['Med_income'].apply(lambda x: int(x))
income['Total_Households'] = income['Total_Households'].apply(lambda x: int(x))
income['Year'] = pd.to_datetime(income.Year, format='%Y').dt.year

In [77]:
income

Year                      County  Total_Households  Med_income state
0     2013              Pike County,KY             25658       34373    KY
1     2013            Warren County,KY             45541       48783    KY
2     2013         Ascension Parish,LA             40762       75308    LA
3     2013           Bossier Parish,LA             47151       51796    LA
4     2013             Caddo Parish,LA             98570       39683    LA
...    ...                         ...               ...         ...   ...
5827  2019          Ponce Municipio,PR             52837       15130    PR
5828  2019       San Juan Municipio,PR            138800       23005    PR
5829  2019       Toa Alta Municipio,PR             22650       28440    PR
5830  2019       Toa Baja Municipio,PR             28291       23368    PR
5831  2019  Trujillo Alto Municipio,PR             23263       32244    PR

[5832 rows x 5 columns]

### interpolating for month value

In [78]:
m_income = pd.DataFrame()
for county, df in income.groupby('County'):
    df['iChange'] = df['Med_income'].diff() / df['Med_income'].shift()
    df['hChange'] = df['Total_Households'].diff() / df['Total_Households'].shift()
    df = df.iloc[np.arange(df.shape[0]).repeat(12)].reset_index().drop('index', axis = 1)
    df = pd.concat([df, pd.DataFrame(list(range(1, 13)) * int(df.shape[0] / 12), columns = ['Month'])], axis = 1)
    df = df[df['Year'] != 2013]
    for year in pd.unique(df['Year']):
        df[df['Year'] == year]['Med_income'] = df[df['Year'] == 2014]['Med_income'] * (((1 + df[df['Year'] == 2014]['iChange']) ** (1/12)) ** df[df['Year'] == 2014]['Month'])
        df[df['Year'] == year]['Total_Households'] = df[df['Year'] == 2014]['Total_Households'] * (((1 + df[df['Year'] == 2014]['hChange']) ** (1/12)) ** df[df['Year'] == 2014]['Month'])
    m_income = pd.concat([m_income, df], axis = 0)

<ipython-input-78-6988c555b619>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[df['Year'] == year]['Med_income'] = df[df['Year'] == 2014]['Med_income'] * (((1 + df[df['Year'] == 2014]['iChange']) ** (1/12)) ** df[df['Year'] == 2014]['Month'])
<ipython-input-78-6988c555b619>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[df['Year'] == year]['Total_Households'] = df[df['Year'] == 2014]['Total_Households'] * (((1 + df[df['Year'] == 2014]['hChange']) ** (1/12)) ** df[df['Year'] == 2014]['Month'])
<ip

<ipython-input-78-6988c555b619>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[df['Year'] == year]['Med_income'] = df[df['Year'] == 2014]['Med_income'] * (((1 + df[df['Year'] == 2014]['iChange']) ** (1/12)) ** df[df['Year'] == 2014]['Month'])
<ipython-input-78-6988c555b619>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[df['Year'] == year]['Total_Households'] = df[df['Year'] == 2014]['Total_Households'] * (((1 + df[df['Year'] == 2014]['hChange']) ** (1/12)) ** df[df['Year'] == 2014]['Month'])
<ip

<ipython-input-78-6988c555b619>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[df['Year'] == year]['Med_income'] = df[df['Year'] == 2014]['Med_income'] * (((1 + df[df['Year'] == 2014]['iChange']) ** (1/12)) ** df[df['Year'] == 2014]['Month'])
<ipython-input-78-6988c555b619>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[df['Year'] == year]['Total_Households'] = df[df['Year'] == 2014]['Total_Households'] * (((1 + df[df['Year'] == 2014]['hChange']) ** (1/12)) ** df[df['Year'] == 2014]['Month'])
<ip

<ipython-input-78-6988c555b619>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[df['Year'] == year]['Med_income'] = df[df['Year'] == 2014]['Med_income'] * (((1 + df[df['Year'] == 2014]['iChange']) ** (1/12)) ** df[df['Year'] == 2014]['Month'])
<ipython-input-78-6988c555b619>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[df['Year'] == year]['Total_Households'] = df[df['Year'] == 2014]['Total_Households'] * (((1 + df[df['Year'] == 2014]['hChange']) ** (1/12)) ** df[df['Year'] == 2014]['Month'])
<ip

<ipython-input-78-6988c555b619>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[df['Year'] == year]['Med_income'] = df[df['Year'] == 2014]['Med_income'] * (((1 + df[df['Year'] == 2014]['iChange']) ** (1/12)) ** df[df['Year'] == 2014]['Month'])
<ipython-input-78-6988c555b619>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[df['Year'] == year]['Total_Households'] = df[df['Year'] == 2014]['Total_Households'] * (((1 + df[df['Year'] == 2014]['hChange']) ** (1/12)) ** df[df['Year'] == 2014]['Month'])
<ip

...

<ipython-input-78-6988c555b619>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[df['Year'] == year]['Med_income'] = df[df['Year'] == 2014]['Med_income'] * (((1 + df[df['Year'] == 2014]['iChange']) ** (1/12)) ** df[df['Year'] == 2014]['Month'])
<ipython-input-78-6988c555b619>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[df['Year'] == year]['Total_Households'] = df[df['Year'] == 2014]['Total_Households'] * (((1 + df[df['Year'] == 2014]['hChange']) ** (1/12)) ** df[df['Year'] == 2014]['Month'])
<ip

<ipython-input-78-6988c555b619>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[df['Year'] == year]['Total_Households'] = df[df['Year'] == 2014]['Total_Households'] * (((1 + df[df['Year'] == 2014]['hChange']) ** (1/12)) ** df[df['Year'] == 2014]['Month'])
<ipython-input-78-6988c555b619>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[df['Year'] == year]['Med_income'] = df[df['Year'] == 2014]['Med_income'] * (((1 + df[df['Year'] == 2014]['iChange']) ** (1/12)) ** df[df['Year'] == 2014]['Month'])
<ip

<ipython-input-78-6988c555b619>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[df['Year'] == year]['Med_income'] = df[df['Year'] == 2014]['Med_income'] * (((1 + df[df['Year'] == 2014]['iChange']) ** (1/12)) ** df[df['Year'] == 2014]['Month'])
<ipython-input-78-6988c555b619>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[df['Year'] == year]['Total_Households'] = df[df['Year'] == 2014]['Total_Households'] * (((1 + df[df['Year'] == 2014]['hChange']) ** (1/12)) ** df[df['Year'] == 2014]['Month'])
<ip

<ipython-input-78-6988c555b619>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[df['Year'] == year]['Med_income'] = df[df['Year'] == 2014]['Med_income'] * (((1 + df[df['Year'] == 2014]['iChange']) ** (1/12)) ** df[df['Year'] == 2014]['Month'])
<ipython-input-78-6988c555b619>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[df['Year'] == year]['Total_Households'] = df[df['Year'] == 2014]['Total_Households'] * (((1 + df[df['Year'] == 2014]['hChange']) ** (1/12)) ** df[df['Year'] == 2014]['Month'])
<ip

<ipython-input-78-6988c555b619>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[df['Year'] == year]['Med_income'] = df[df['Year'] == 2014]['Med_income'] * (((1 + df[df['Year'] == 2014]['iChange']) ** (1/12)) ** df[df['Year'] == 2014]['Month'])
<ipython-input-78-6988c555b619>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[df['Year'] == year]['Total_Households'] = df[df['Year'] == 2014]['Total_Households'] * (((1 + df[df['Year'] == 2014]['hChange']) ** (1/12)) ** df[df['Year'] == 2014]['Month'])
<ip

In [79]:
#(2018-2017)/12*1 for january.. (2018-2017)/12**2 to feb.. *3... and so forth

In [80]:
m_income

Year          County  Total_Households  Med_income state   iChange  \
12  2014   Ada County,ID            159896       57716    ID  0.098474   
13  2014   Ada County,ID            159896       57716    ID  0.098474   
14  2014   Ada County,ID            159896       57716    ID  0.098474   
15  2014   Ada County,ID            159896       57716    ID  0.098474   
16  2014   Ada County,ID            159896       57716    ID  0.098474   
..   ...             ...               ...         ...   ...       ...   
79  2019  Yuma County,AZ             74042       46419    AZ  0.069488   
80  2019  Yuma County,AZ             74042       46419    AZ  0.069488   
81  2019  Yuma County,AZ             74042       46419    AZ  0.069488   
82  2019  Yuma County,AZ             74042       46419    AZ  0.069488   
83  2019  Yuma County,AZ             74042       46419    AZ  0.069488   

     hChange  Month  
12  0.028707      1  
13  0.028707      2  
14  0.028707      3  
15  0.028707      4  
16  0.028707      5  
..       ...    ...  
79 -0.006574      8  
80 -0.006574      9  
81 -0.006574     10  
82 -0.006574     11  
83 -0.006574     12  

[60048 rows x 8 columns]